In [10]:
%uv pip install pymongo

Using Python 3.12.6 environment at: /usr/local
Audited 1 package in 11ms
Note: you may need to restart the kernel to use updated packages.


In [11]:
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import IterableDataset, DataLoader
from pymongo import MongoClient
from pymongo.server_api import ServerApi
import numpy as np
from tqdm import tqdm
import hashlib


In [12]:
uri = "mongodb+srv://22nwd3_db_user:<passwprd>@lichessgames.c2mdjob.mongodb.net/?appName=lichessGames"
client = MongoClient(uri, server_api=ServerApi('1'))
db = client["lichessGames"]
collection = db["2015-04"]

try:
    client.admin.command('ping')
    print("Connected to MongoDB!")
except Exception as e:
    print(e)


Connected to MongoDB!


In [13]:
def coords_to_tensor(coords, augment=False):
    tensor = np.zeros((12, 8, 8), dtype=np.float32)
    for c, r, col in coords:
        tensor[c, r, col] = 1.0

    if augment:
        # horizontal flip
        if np.random.rand() > 0.5:
            tensor = np.flip(tensor, axis=2).copy()
        # vertical flip (optional, less common in chess)
        if np.random.rand() > 0.5:
            tensor = np.flip(tensor, axis=1).copy()

    return tensor

In [14]:
class ChessMongoDataset(IterableDataset):
    def __init__(self, collection, split="train", train_frac=0.9, max_samples=None, augment=False):
        self.collection = collection
        self.split = split
        self.train_frac = train_frac
        self.max_samples = max_samples
        self.augment = augment

    def __iter__(self):
        cursor = self.collection.find({}, no_cursor_timeout=True)
        count = 0
        for doc in cursor:
            # deterministic split
            doc_hash = int(hashlib.md5(str(doc["_id"]).encode()).hexdigest(), 16)
            if self.split == "train" and (doc_hash % 100 >= int(self.train_frac * 100)):
                continue
            if self.split == "val" and (doc_hash % 100 < int(self.train_frac * 100)):
                continue

            coords = doc.get("tensor")
            if not coords:
                continue
            tensor = coords_to_tensor(coords, augment=self.augment)

            eval_val = doc.get("eval")
            if eval_val is None:
                continue  # skip checkmate

            eval_norm = float(np.tanh(eval_val / 100.0))  # tanh normalization

            yield torch.tensor(tensor, dtype=torch.float32), torch.tensor(eval_norm, dtype=torch.float32)

            count += 1
            if self.max_samples and count >= self.max_samples:
                break
        cursor.close()



In [15]:
batch_size = 64
# train_dataset = ChessMongoDataset(collection, split="train", augment=True)
# val_dataset   = ChessMongoDataset(collection, split="val", augment=False)
train_dataset = ChessMongoDataset(collection, split="train", augment=True, max_samples=100_000)
val_dataset = ChessMongoDataset(collection, split="val", max_samples=10_000)


train_loader = DataLoader(train_dataset, batch_size=batch_size, num_workers=3, prefetch_factor=None)
val_loader   = DataLoader(val_dataset, batch_size=batch_size, num_workers=3, prefetch_factor=None)

print("Dataloaders ready.")


Dataloaders ready.


In [16]:
class ChessCNN(nn.Module):
    def __init__(self):
        super().__init__()
        self.conv1 = nn.Conv2d(12, 16, 3, padding=1)
        self.bn1   = nn.BatchNorm2d(16)
        self.conv2 = nn.Conv2d(16, 32, 3, padding=1)
        self.bn2   = nn.BatchNorm2d(32)
        self.conv3 = nn.Conv2d(32, 64, 3, padding=1)
        self.bn3   = nn.BatchNorm2d(64)

        self.fc1 = nn.Linear(64, 64)
        self.fc2 = nn.Linear(64, 1)

        self.act = nn.LeakyReLU(0.1)

    def forward(self, x):
        x = self.act(self.bn1(self.conv1(x)))
        x = self.act(self.bn2(self.conv2(x)))
        x = self.act(self.bn3(self.conv3(x)))
        x = F.adaptive_avg_pool2d(x, (1, 1))  # 64x1x1
        x = x.view(x.size(0), -1)             # flatten
        x = self.act(self.fc1(x))
        return self.fc2(x)

In [17]:
device = "cuda" if torch.cuda.is_available() else "cpu"
model = ChessCNN().to(device)

optimizer = torch.optim.Adam(model.parameters(), lr=1e-3)
loss_fn = torch.nn.SmoothL1Loss()  # robust Huber loss
scaler = torch.amp.GradScaler()

epochs = 20
checkpoint_path = "chess_cnn_best.pth"

# Optional learning rate scheduler
from torch.optim.lr_scheduler import ReduceLROnPlateau
scheduler = ReduceLROnPlateau(optimizer, mode='min', factor=0.5, patience=3)

# Early stopping
early_stop_patience = 5
best_val_loss = float('inf')
no_improve_epochs = 0


In [18]:
from torch.amp import autocast, GradScaler

scaler = GradScaler()
best_val_loss = float('inf')
no_improve_epochs = 0
early_stop_patience = 5

for epoch in range(epochs):
    # -----------------------
    # Training
    # -----------------------
    model.train()
    train_loss_sum = 0.0
    train_batches = 0

    loader = tqdm(train_loader, desc=f"Epoch {epoch+1} [Train]", leave=False)
    for xb, yb in loader:
        xb, yb = xb.to(device), yb.to(device)

        optimizer.zero_grad()
        with autocast(device_type="cuda"):
            pred = model(xb)
            loss = loss_fn(pred.squeeze(), yb)

        scaler.scale(loss).backward()
        scaler.step(optimizer)
        scaler.update()

        train_loss_sum += loss.item()
        train_batches += 1
        loader.set_postfix(train_loss=train_loss_sum / train_batches)

    train_loss = train_loss_sum / max(train_batches, 1)

    # -----------------------
    # Validation
    # -----------------------
    model.eval()
    val_loss_sum = 0.0
    val_batches = 0

    vloader = tqdm(val_loader, desc=f"Epoch {epoch+1} [Val]", leave=False)
    with torch.no_grad():
        for xb, yb in vloader:
            xb, yb = xb.to(device), yb.to(device)
            with autocast(device_type="cuda"):
                pred = model(xb)
                val_loss_sum += loss_fn(pred.squeeze(), yb).item()
                val_batches += 1
            vloader.set_postfix(val_loss=val_loss_sum / max(val_batches,1))

    val_loss = val_loss_sum / max(val_batches, 1)
    print(f"Epoch {epoch+1}: train_loss={train_loss:.4f}, val_loss={val_loss:.4f}")

    # -----------------------
    # Scheduler step
    # -----------------------
    scheduler.step(val_loss)
    lr = optimizer.param_groups[0]['lr']
    print(f"Current learning rate: {lr:.6f}")

    # -----------------------
    # Checkpointing + early stopping
    # -----------------------
    if val_loss < best_val_loss:
        best_val_loss = val_loss
        torch.save(model.state_dict(), checkpoint_path)
        print(f"Validation improved. Saved checkpoint to {checkpoint_path}")
        no_improve_epochs = 0
    else:
        no_improve_epochs += 1
        if no_improve_epochs >= early_stop_patience:
            print("Early stopping triggered.")
            break

print("Training complete.")
print(f"Best model saved at: {checkpoint_path}")


Epoch 1 [Train]: 0it [00:00, ?it/s]/usr/local/lib/python3.12/site-packages/pymongo/synchronous/collection.py:1954: UserWarning: use an explicit session with no_cursor_timeout=True otherwise the cursor may still timeout after 30 minutes, for more info see https://mongodb.com/docs/v4.4/reference/method/cursor.noCursorTimeout/#session-idle-timeout-overrides-nocursortimeout
  return Cursor(self, *args, **kwargs)
/usr/local/lib/python3.12/site-packages/pymongo/synchronous/collection.py:1954: UserWarning: use an explicit session with no_cursor_timeout=True otherwise the cursor may still timeout after 30 minutes, for more info see https://mongodb.com/docs/v4.4/reference/method/cursor.noCursorTimeout/#session-idle-timeout-overrides-nocursortimeout
  return Cursor(self, *args, **kwargs)
/usr/local/lib/python3.12/site-packages/pymongo/synchronous/collection.py:1954: UserWarning: use an explicit session with no_cursor_timeout=True otherwise the cursor may still timeout after 30 minutes, for more 

Epoch 1: train_loss=0.2593, val_loss=0.2308
Current learning rate: 0.001000
Validation improved. Saved checkpoint to chess_cnn_best.pth


Epoch 2 [Train]: 0it [00:00, ?it/s]/usr/local/lib/python3.12/site-packages/pymongo/synchronous/collection.py:1954: UserWarning: use an explicit session with no_cursor_timeout=True otherwise the cursor may still timeout after 30 minutes, for more info see https://mongodb.com/docs/v4.4/reference/method/cursor.noCursorTimeout/#session-idle-timeout-overrides-nocursortimeout
  return Cursor(self, *args, **kwargs)
/usr/local/lib/python3.12/site-packages/pymongo/synchronous/collection.py:1954: UserWarning: use an explicit session with no_cursor_timeout=True otherwise the cursor may still timeout after 30 minutes, for more info see https://mongodb.com/docs/v4.4/reference/method/cursor.noCursorTimeout/#session-idle-timeout-overrides-nocursortimeout
  return Cursor(self, *args, **kwargs)
/usr/local/lib/python3.12/site-packages/pymongo/synchronous/collection.py:1954: UserWarning: use an explicit session with no_cursor_timeout=True otherwise the cursor may still timeout after 30 minutes, for more 

Epoch 2: train_loss=0.2230, val_loss=0.2034
Current learning rate: 0.001000
Validation improved. Saved checkpoint to chess_cnn_best.pth


Epoch 3 [Train]: 0it [00:00, ?it/s]/usr/local/lib/python3.12/site-packages/pymongo/synchronous/collection.py:1954: UserWarning: use an explicit session with no_cursor_timeout=True otherwise the cursor may still timeout after 30 minutes, for more info see https://mongodb.com/docs/v4.4/reference/method/cursor.noCursorTimeout/#session-idle-timeout-overrides-nocursortimeout
  return Cursor(self, *args, **kwargs)
/usr/local/lib/python3.12/site-packages/pymongo/synchronous/collection.py:1954: UserWarning: use an explicit session with no_cursor_timeout=True otherwise the cursor may still timeout after 30 minutes, for more info see https://mongodb.com/docs/v4.4/reference/method/cursor.noCursorTimeout/#session-idle-timeout-overrides-nocursortimeout
  return Cursor(self, *args, **kwargs)
/usr/local/lib/python3.12/site-packages/pymongo/synchronous/collection.py:1954: UserWarning: use an explicit session with no_cursor_timeout=True otherwise the cursor may still timeout after 30 minutes, for more 

...

Epoch 18: train_loss=0.1663, val_loss=0.1555
Current learning rate: 0.001000


Epoch 19 [Train]: 0it [00:00, ?it/s]/usr/local/lib/python3.12/site-packages/pymongo/synchronous/collection.py:1954: UserWarning: use an explicit session with no_cursor_timeout=True otherwise the cursor may still timeout after 30 minutes, for more info see https://mongodb.com/docs/v4.4/reference/method/cursor.noCursorTimeout/#session-idle-timeout-overrides-nocursortimeout
  return Cursor(self, *args, **kwargs)
/usr/local/lib/python3.12/site-packages/pymongo/synchronous/collection.py:1954: UserWarning: use an explicit session with no_cursor_timeout=True otherwise the cursor may still timeout after 30 minutes, for more info see https://mongodb.com/docs/v4.4/reference/method/cursor.noCursorTimeout/#session-idle-timeout-overrides-nocursortimeout
  return Cursor(self, *args, **kwargs)
/usr/local/lib/python3.12/site-packages/pymongo/synchronous/collection.py:1954: UserWarning: use an explicit session with no_cursor_timeout=True otherwise the cursor may still timeout after 30 minutes, for more

Epoch 19: train_loss=0.1647, val_loss=0.1517
Current learning rate: 0.001000
Validation improved. Saved checkpoint to chess_cnn_best.pth


Epoch 20 [Train]: 0it [00:00, ?it/s]/usr/local/lib/python3.12/site-packages/pymongo/synchronous/collection.py:1954: UserWarning: use an explicit session with no_cursor_timeout=True otherwise the cursor may still timeout after 30 minutes, for more info see https://mongodb.com/docs/v4.4/reference/method/cursor.noCursorTimeout/#session-idle-timeout-overrides-nocursortimeout
  return Cursor(self, *args, **kwargs)
/usr/local/lib/python3.12/site-packages/pymongo/synchronous/collection.py:1954: UserWarning: use an explicit session with no_cursor_timeout=True otherwise the cursor may still timeout after 30 minutes, for more info see https://mongodb.com/docs/v4.4/reference/method/cursor.noCursorTimeout/#session-idle-timeout-overrides-nocursortimeout
  return Cursor(self, *args, **kwargs)
/usr/local/lib/python3.12/site-packages/pymongo/synchronous/collection.py:1954: UserWarning: use an explicit session with no_cursor_timeout=True otherwise the cursor may still timeout after 30 minutes, for more

Epoch 20: train_loss=0.1629, val_loss=0.1514
Current learning rate: 0.001000
Validation improved. Saved checkpoint to chess_cnn_best.pth
Training complete.
Best model saved at: chess_cnn_best.pth
